# Mega API 測試 Notebook

## 1. 限制

1. 複委託無跨日預約單功能
2. 如在其他平台的委託(如兆豐贏家、理財通等...)，API會收不到主動回報及成交回報，但可以用API的委託查詢、成交查詢查到委託狀態，並可刪改單
3. 每秒委託限制10筆，超過的委託會被拒絕

## 2. 測試環境下單

1. 下單時間: 11:00~18:00
2. 開通正式環境使用權限以前，開通證券的客戶至少需完成測試環境委託刪單、成交測試
3. 成交股數1~1000股、不成交股數2000股、部分成交股數2700股
4. 下單商品可從E網通或行動VIP查詢，可以從API取得

## 3. 範例需修改地方

第一個程式區塊，修改個人資料



## 4. 正式環境連線
當測試報告書完成後且收到公司通知已開通，如要下單到正式環境需修改以下兩個連線

1. speedyAPI_config.json裡的spapitest 改為 spapi
2. ObjOrder.Connect 裡的 spapitest 改為 spapi





## 5. Notebook 說明
本 Notebook 將證券、期貨及選擇權的委託、刪單、改單（改價或減量）測試流程拆分為多個 Cell。
每個 Cell 都會使用預先定義好的參數進行測試，並利用 logging 輸出回報訊息，
方便確認委託與成交回報是否正確。

**注意：**
1. 委託成功後，回報中的 `OrderID` 與 `SendNewOrderEx` 回傳的 `nid` 不同；
   刪單及改單時必須使用回調中的 `OrderID`。
2. 各市場的參數有所不同，例如證券下單的 TWSEOrdTyp 為 "0"；
   期貨及選擇權下單中部分參數需留空（例如期貨的 TWSEOrdTyp 為空字串）。

## 6. 其他知識點
- **Python 模組與 package：**
  本程式碼使用了 Mega API 的 Python package（例如 `megaSpeedy.spdOrderAPI`），
  並假設你已依照官方說明將相應 package 放置到 Python 的環境中（或虛擬環境內的 site-packages 目錄）。
- **logging 模組：**
  用於記錄訊息與除錯資訊，設定了輸出格式與等級，方便觀察程式執行狀態。
- **回傳結果處理：**
  API 回傳的結果通常為 JSON 格式，利用 `json.dumps` 可以格式化輸出，
  而使用 Pandas 將 list 轉 DataFrame 可方便檢視資料表格形式的內容。


In [7]:
import time
import os
import logging

# 設定 logging 格式與等級
logging.basicConfig(level=logging.INFO, format='%(asctime)s %(levelname)s: %(message)s')
logging.info('初始化環境完成')


# 請將以下變數值，改為自己的資料
UID='A123456789' #身分證字號字母大寫
LoginPW='1234' #登入密碼
SKBranchid='7000' #分公司別 7000為總公司
SKAcc='123456' #證券帳號
CAPath='1234.pfx' #憑證路徑
CAPW='A123456789' #憑證密碼，測試環境預設同身分證字號



2025-04-15 10:38:45,894 INFO: 初始化環境完成


In [8]:
from megaSpeedy.spdOrderAPI import spdOrderAPI

class testPyOrderAPI(spdOrderAPI):
    """
    Speedy API 測試類別
    此類別繼承自官方提供的 spdOrderAPI，並覆寫了部分回調函式
    以便在委託下單、刪單、改單及成交回報時，能夠記錄詳細資訊。
    """
    def __init__(self):
        # 呼叫父類別建構子以初始化底層 API 連結
        super().__init__()
        self.FIsLogon = False
        self.lastOrderID = None  # 用來儲存最新委託回報中的 OrderID，供取消或改單使用
        

    def OnConnected(self):
        logging.info('-------------- OnConnected() --------------')
        # 使用憑證內的帳號 (此處範例使用 "A123456789")
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0123456]')
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '期貨帳號七位數如:[0023456]')
        # 登入證期市場逗號分隔
        # self.LogonProxy('身分證字號(大寫字母)', '電子登入密碼', '證券帳號七位數如:[0123456],期貨帳號七位數如:[0023456]')
        # self.LogonProxy('A123456789', '4567', '0123456,0023456')
        if not self.LogonProxy(UID, LoginPW, SKAcc ):
            logging.error(f'登入失敗! {self.GetLastErrorMsg()}')
            raise Exception("條件不符，中斷執行！")



    def OnDisconnected(self):
        logging.info('-------------- OnDisconnected() --------------')
        self.FIsLogon = False

    def OnLogonResponse(self, IsSucceed, ReplyString):
        logging.info('-------------- OnLogonResponse() --------------')
        logging.info(f'--- IsSucceed: {IsSucceed} ReplyString: {ReplyString}')
        if IsSucceed:
            self.FIsLogon = True
            # 設定各市場下單帳號
            # self.SetAccount( '市場', '分公司別', '帳號')
            self.SetAccount('TAIFEX', 'F030000', '0023456')  # 期貨帳號 公司別固定為F030000
            self.SetAccount('TWSE', '7000', '0023456' )        # 證券帳號 公司別依照下單帳號的公司別
            self.SetAccount('US', SKBranchid, SKAcc )           # 複委託帳號
        else:
            logging.error(f"登入失敗. {ReplyString}")

    def OnReplyNewOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyNewOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')
        # 儲存回報中的 OrderID 以便後續取消或改單時使用
        self.lastOrderID = OrderID

    def OnReplyCancelOrder(self, NID, UDD, Symbol, Price, Side, OrderID):
        logging.info('-------------- OnReplyCancelOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side} OrderID: {OrderID}')

    def OnReplyReplaceOrder(self, NID, UDD, Symbol, Price, Side, OrderQty, OrderType, TimeInForce, OrderID):
        logging.info('-------------- OnReplyReplaceOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} Symbol: {Symbol} Price: {Price} Side: {Side}')
        logging.info(f'--- OrderQty: {OrderQty} OrderType: {OrderType} TimeInForce: {TimeInForce} OrderID: {OrderID}')

    def OnRejectOrder(self, NID, UDD, ActionFrom, ErrCode, ErrMsg):
        logging.info('-------------- OnRejectOrder() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} ActionFrom: {ActionFrom} ErrCode: {ErrCode} ErrMsg: {ErrMsg}')

    def OnFill(self, NID, UDD, OrderID, ReportSequence, FillPrice, FillQty, FillTime):
        logging.info('-------------- OnFill() --------------')
        logging.info(f'--- NID: {NID} UDD: {UDD} OrderID: {OrderID} ReportSequence: {ReportSequence}')
        logging.info(f'--- FillPrice: {FillPrice} FillQty: {FillQty} FillTime: {FillTime}')


In [9]:
# 實例化 API 物件，並設定憑證
# 請確保 A123456789.pfx 憑證檔案放置於工作目錄下
#ObjOrder.EnableMEGACA("憑證檔路徑","身分證字號(大寫字母)","憑證密碼")
ObjOrder = testPyOrderAPI()
result = ObjOrder.EnableMEGACA(CAPath, UID, CAPW)
if result:
    logging.info('已成功設定簽章憑證')
    logging.info('連線中...')
else:
    logging.error(f'簽章憑證設定失敗! {ObjOrder.GetLastErrorMsg()}')
    raise Exception("條件不符，中斷執行！")

# 複委託使用port為56790
ObjOrder.Connect('spapitest.emega.com.tw', 56790, 5)



#以下為自動重連範例，請先確認個人資料都正確才使用，不然帳號會因為錯誤次數太多而被鎖定
"""
Count = 0
while True:
    time.sleep(1)
    if Count % 10 == 0:
        if not ObjOrder.IsConnected():
            ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)
    Count += 1
    if ObjOrder.FIsLogon:
        logging.info('登入成功！')
        break
logging.info('連線及登入程序完成')
"""

2025-04-15 10:38:47,252 INFO: 已成功設定簽章憑證
2025-04-15 10:38:47,252 INFO: 連線中...


"\nCount = 0\nwhile True:\n    time.sleep(1)\n    if Count % 10 == 0:\n        if not ObjOrder.IsConnected():\n            ObjOrder.Connect('spapitest.emega.com.tw', 56789, 5)\n    Count += 1\n    if ObjOrder.FIsLogon:\n        logging.info('登入成功！')\n        break\nlogging.info('連線及登入程序完成')\n"

2025-04-15 10:38:47,650 INFO: -------------- OnConnected() --------------
2025-04-15 10:38:48,053 INFO: -------------- OnLogonResponse() --------------
2025-04-15 10:38:48,055 INFO: --- IsSucceed: True ReplyString: Login Mega DMA OK!( CID =11 )...logon ok


## 證券測試流程 (請依序執行下面各個 Cell)

In [10]:
# 複委託新單委託測試
securities_order = {
    "Market": "USS",         # 市場 US:美股 USS:美股每股 ，要大寫
    "Symbol": "NVDA",        # 股票代號 NVDA
    "Price": 1,             # 委託價格 (示例價格)
    "StopPrice": 0,             # 委託價格 (示例價格)
    "Qty": 2000,                  # 委託股數
    "Side": "B",             # 買進委託 ("B" 為買，"S" 為賣)
    "OrderType": "L",        # L:Limit M:Market SL:StopLimit
    "Tif": "R",              # 當日有效 (ROD)
    "CS": "1",               # [Currency] (1:TWD 2:NON-TWD)
    "EI": "",               # [ExecInst] (G:AON  全部成交否則取消 ，空字串:不限)
}

securities_new_nid = ObjOrder.SendNewForeignOrder(
    securities_order["Market"],
    "testUDD_New",
    securities_order["Symbol"],
    securities_order["Price"],
    securities_order["StopPrice"],
    securities_order["Side"],
    securities_order["Qty"],
    securities_order["OrderType"],
    securities_order["Tif"],
    securities_order["CS"],
    securities_order["EI"]
)

if securities_new_nid == 0:
    logging.error(f"複委託新單委託失敗: {ObjOrder.GetLastErrorMsg()}")
else:
    logging.info(f"複委託新單委託成功, nid={securities_new_nid}")


2025-04-15 10:38:56,727 INFO: 複委託新單委託成功, nid=89
2025-04-15 10:39:04,765 INFO: -------------- OnReplyNewOrder() --------------
2025-04-15 10:39:04,771 INFO: --- NID: 89 UDD:  Symbol: NVDA Price: 1.0 Side: B
2025-04-15 10:39:04,773 INFO: --- OrderQty: 2000 OrderType: L TimeInForce: R OrderID: S09NKUed


In [11]:
# 複委託刪單委託測試
# 使用從新單回調中取得的 OrderID
if ObjOrder.lastOrderID is None:
    logging.error('未取得複委託新單回報的 OrderID，無法執行刪單測試')
else:
    cancel_order_sec = {
        "Market": securities_order["Market"],
        "Symbol": securities_order["Symbol"],        
        "Side": securities_order["Side"],  # 與下單時相同
        "OrderID": ObjOrder.lastOrderID,     # 使用回報中的訂單編號       
    }
    
    securities_cancel_nid = ObjOrder.SendCancelForeignOrder(
        cancel_order_sec["Market"],
        "testUDD_Cancel",
        cancel_order_sec["Symbol"],       
        cancel_order_sec["Side"],
        cancel_order_sec["OrderID"]    
    )
    
    if securities_cancel_nid == 0:
        logging.error(f"複委託刪單委託失敗: {ObjOrder.GetLastErrorMsg()}")
    else:
        logging.info(f"複委託刪單委託成功, nid={securities_cancel_nid}")


2025-04-15 10:39:09,948 INFO: 複委託刪單委託成功, nid=90
2025-04-15 10:39:11,345 INFO: -------------- OnReplyCancelOrder() --------------
2025-04-15 10:39:11,348 INFO: --- NID: 90 UDD:  Symbol: NVDA Price: 1.0 Side: B OrderID: S09NKUed


In [17]:
import json
import pandas as pd

# 複委託委託查詢測試
# 建立查詢參數，所有參數皆以字串表示
query_param = {
    "branch_id": SKBranchid,       # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,       # 客戶帳號 (必填)，請依實際情況設定
    "qry_kind": "0",         
}

# 呼叫 queryForeignStockOrder 進行複委託委託查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryForeignStockOrder(query_param)


# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("複委託委託查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 若 api_result 中有委託資料 (dataList)，將其轉為 DataFrame 表格顯示，方便閱讀
if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
else:
    logging.info("查詢結果中無委託資料")


複委託委託查詢結果:
"{\"result\":\"0\",\"dataList\":[{\"date\":\"20250414\",\"errcode\":\"\",\"msg\":\"\",\"symbol\":\"NVDA\",\"lastshares\":\"0\",\"ordtype\":\"2\",\"leavesqty\":\"0\",\"starttime\":\"\",\"type\":\"1\",\"act\":\"N\",\"price\":\"1.0\",\"execinst\":\"\",\"msgtype\":\"N\",\"stopprice\":\"0.0\",\"ip\":\"\",\"bhno\":\"7000\",\"errmsg\":\"\",\"ordertime\":\"\",\"delqty\":\"2000\",\"tdate\":\"20250414\",\"execrefid\":\"\",\"orderqty\":\"2000\",\"origclordid\":\"\",\"pegdifference\":\"0.000000\",\"status\":\"\",\"lastpx\":\"1.0\",\"orderdate\":\"\",\"execid\":\"\",\"mqack\":\"\",\"orderkind\":\"STD\",\"se\":\"US\",\"clordid\":\"S04gfFzc\",\"timeinforce\":\"0\",\"origsrc\":\"PI\",\"fixno\":\"16\",\"ordstusno\":\"C\",\"currency\":\"1\",\"sename\":\"美股\",\"side\":\"1\",\"securitydesc\":\"\",\"stknm\":\"輝達\",\"orderid\":\"BV19094578\",\"ordstusnm\":\"刪單成功 \",\"endtime\":\"\",\"execsrc\":\"PI\",\"useracc\":\"123456\",\"target\":\"VTHB\",\"currname\":\"美元\",\"volumerate\":\"0.00\",\"time\":\

date errcode msg symbol lastshares ordtype leavesqty starttime type  \
0  20250414               NVDA          0       2         0              1   
1  20250414               NVDA          1       2         0              1   

  act  ... ordstusnm endtime execsrc useracc target currname volumerate  \
0   N  ...     刪單成功               PI  123456   VTHB       美元       0.00   
1   N  ...      完全成交              PI  123456   VTHB       美元       0.00   

     time strategy    account  
0  152501           TRMEGAFIX  
1  152056           TRMEGAFIX  

[2 rows x 52 columns]

In [18]:
import json
import pandas as pd  # 請先安裝 pandas 套件 (pip install pandas)

# 複委託成交查詢測試
# 建立查詢參數 (所有參數皆以字串表示)
query_param = {
    "branch_id": SKBranchid,       # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,       # 客戶帳號 (必填)，請依實際情況設定       
}

# 呼叫 queryForeignStockFilled 進行證券成交查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryForeignStockFilled(query_param)

# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("複委託成交查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 若 api_result 中有成交明細 (dataList)，將其轉成 DataFrame 表格顯示
if "dataList" in api_result and api_result["dataList"]:
    df = pd.DataFrame(api_result["dataList"])
    display(df)
else:
    logging.info("查詢結果中無成交資料")


複委託成交查詢結果:
"{\"result\":\"0\",\"dataList\":[{\"date\":\"20250414\",\"errcode\":\"\",\"symbol\":\"NVDA\",\"lastshares\":\"1\",\"lastpx\":\"1.0\",\"ordtype\":\"2\",\"leavesqty\":\"0\",\"type\":\"1\",\"execid\":\"US.00000000000006734390\",\"mqack\":\"\",\"orderkind\":\"STD\",\"se\":\"US\",\"act\":\"N\",\"clordid\":\"S04gfFSa\",\"price\":\"1.0\",\"timeinforce\":\"0\",\"origsrc\":\"PI\",\"execinst\":\"\",\"fixno\":\"15\",\"currency\":\"1\",\"msgtype\":\"F\",\"sename\":\"美股\",\"stopprice\":\"0.0\",\"side\":\"1\",\"cost\":\"1.00\",\"orderid\":\"BV19094566\",\"bhno\":\"7000\",\"errmsg\":\"FILLED\",\"execsrc\":\"PI\",\"useracc\":\"123456\",\"target\":\"VTHB\",\"currname\":\"美元\",\"tdate\":\"20250414\",\"execrefid\":\"\",\"orderqty\":\"1\",\"time\":\"152056\",\"origclordid\":\"\",\"account\":\"TRMEGAFIX\"}],\"message\":\"執行成功\"}"


date errcode symbol lastshares lastpx ordtype leavesqty type  \
0  20250414           NVDA          1    1.0       2         0    1   

                    execid mqack  ... execsrc useracc target currname  \
0  US.00000000000006734390        ...      PI  123456   VTHB       美元   

      tdate execrefid orderqty    time origclordid    account  
0  20250414                  1  152056              TRMEGAFIX  

[1 rows x 38 columns]

In [21]:
import json
import pandas as pd

# 複委託帳務查詢測試
# 建立查詢參數 (所有參數皆以字串表示)
query_param = {
    "branch_id": SKBranchid,         # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,         # 客戶帳號 (必填)

}

# 呼叫 queryForeignStockInventory 進行複委託帳務查詢，回傳結果為 JSON 格式
api_result = ObjOrder.queryForeignStockInventory(query_param)

# 使用 json.dumps 格式化輸出查詢結果
pretty_result = json.dumps(api_result, indent=4, ensure_ascii=False)
print("複委託帳務查詢結果:")
print(pretty_result)

api_result = json.loads(api_result)

# 如果 api_result 中包含 outDetailList ，將其轉成 DataFrame 表格顯示

if "outDetailList" in api_result and api_result["outDetailList"]:
    df = pd.DataFrame(api_result["outDetailList"])
    display(df)
else:
    logging.info("查詢結果中無帳務資料")


複委託帳務查詢結果:
"{\"result\":\"0\",\"outHeaderList\":[{\"tdate\":\"2025/04/14\",\"rtncnt\":\"9\",\"actno\":\"123456\",\"ttime\":\"15:33:08\",\"rtnmsg\":\"成功\",\"rtncode\":\"0000\",\"actname\":\"劉俊*\"}],\"outDetailList\":[{\"stkno\":\"AVGO\",\"stkname\":\"安華高科技公司\",\"curysttl\":\"TWD\",\"tsqty\":\"0.000000\",\"csqty\":\"4\",\"dsqty\":\"0.000000\",\"curyname1\":\"美元\",\"unit\":\"1\",\"areano\":\"3\",\"curyname\":\"臺幣\",\"areanm\":\"美股\",\"qty\":\"4\",\"dbqty\":\"0.000000\",\"cury\":\"USD\",\"tbqty\":\"0.000000\"},{\"stkno\":\"AVGO\",\"stkname\":\"安華高科技公司\",\"curysttl\":\"USD\",\"tsqty\":\"0.000000\",\"csqty\":\"2152\",\"dsqty\":\"0.000000\",\"curyname1\":\"美元\",\"unit\":\"1\",\"areano\":\"3\",\"curyname\":\"美元\",\"areanm\":\"美股\",\"qty\":\"2152\",\"dbqty\":\"0.000000\",\"cury\":\"USD\",\"tbqty\":\"0.000000\"},{\"stkno\":\"INTC\",\"stkname\":\"英特爾\",\"curysttl\":\"TWD\",\"tsqty\":\"0.000000\",\"csqty\":\"2409\",\"dsqty\":\"0.000000\",\"curyname1\":\"美元\",\"unit\":\"1\",\"areano\":\"3\",\"curyn

stkno  stkname curysttl     tsqty   csqty     dsqty curyname1 unit areano  \
0  AVGO  安華高科技公司      TWD  0.000000       4  0.000000        美元    1      3   
1  AVGO  安華高科技公司      USD  0.000000    2152  0.000000        美元    1      3   
2  INTC      英特爾      TWD  0.000000    2409  0.000000        美元    1      3   
3  INTC      英特爾      USD  0.000000      66  0.000000        美元    1      3   
4   MMM       3M      TWD  0.000000       4  0.000000        美元    1      3   
5   MMM       3M      USD  0.000000    3504  0.000000        美元    1      3   
6  NVDA       輝達      TWD  0.000000  103277  0.000000        美元    1      3   
7  NVDA       輝達      USD  0.000000    5906  0.000000        美元    1      3   
8  TSLA      特斯拉      TWD  0.000000       1  0.000000        美元    1      3   

  curyname areanm     qty     dbqty cury     tbqty  
0       臺幣     美股       4  0.000000  USD  0.000000  
1       美元     美股    2152  0.000000  USD  0.000000  
2       臺幣     美股    2409  0.000000  USD  0.000000  
3       美元     美股      66  0.000000  USD  0.000000  
4       臺幣     美股       4  0.000000  USD  0.000000  
5       美元     美股    3504  0.000000  USD  0.000000  
6       臺幣     美股  103276  1.000000  USD  1.000000  
7       美元     美股    5906  0.000000  USD  0.000000  
8       臺幣     美股       1  0.000000  USD  0.000000

In [28]:
import json
import pandas as pd


query_param = {
    "branch_id": SKBranchid,         # 分公司代碼 (必填)，證券市場總公司代碼為 7000
    "cust_id": SKAcc,         # 客戶帳號 (必填)
    'keyword':'NVIDIA' #輸入英文公司名稱大寫
}


api_result = ObjOrder.downloadForeignStockProductData(query_param,'comm')


logging.info("複委託商品結果:")
logging.info(api_result)
logging.info("請至工作目錄下查看comm的壓縮檔")



2025-04-14 15:48:17,704 INFO: 複委託商品結果:
2025-04-14 15:48:17,705 INFO: {"result":"0","message":"執行成功"}
2025-04-14 15:48:17,706 INFO: 請至工作目錄下查看comm的壓縮檔


# 中斷連線

釋放資源

In [52]:
# 測試完畢後斷線並結束程序
ObjOrder.Disconnect()
logging.info('~~~ Program terminate ~~~')

2025-04-14 13:35:46,602 INFO: -------------- OnDisconnected() --------------
2025-04-14 13:35:46,604 INFO: ~~~ Program terminate ~~~
